In [1]:
%cd ..

/home/seb/Perso/git/sudoku/sudoku_clean_v2


### Roadmap
- on definit le process de prediction 
- on en deduit le process d'entrainement
- definit un systeme de buffer pour enregistrer X,Y,profondeur
- on code le buffer
- on code l'entrainement pour iterer sur le buffer
- 

## Chose envisager
- on garde les meme buffer/dataloader mais, on en a autant que de profondeurs
- c'est au moment de l'entrainement qu'on choisi sur quel dataloader tapé en fonction de leur profondeur.
- lorsque le niveau 0 est vide on tape sur le plus haut niveau non vide -> non on tape sur le plus peuplé ou on s'en fout


In [2]:
import torch
import pytorch_lightning as pl
from torch import nn
import torch.nn.functional as F
import pandas as pd
import seaborn as sn
import matplotlib.pyplot as plt

from sudoku.models import SmallNetBis, SymPreprocess
from sudoku.loader import DataIterBuffer, train_dataset, test_dataset, data_loader, get_datasets
from sudoku.helper import display_as_dataframe, get_grid_number_soluce
from sudoku.train import SudokuLightning, SudokuTrialErrorLightning

from collections import deque
from typing import Tuple


from torchmetrics import AUROC
from torch.utils.data.dataset import IterableDataset
from torch.utils.data import  DataLoader

from pytorch_lightning.callbacks import ModelCheckpoint
from lightning_lite.utilities.seed import seed_everything

import numpy as np


import math
def sigmoid(x):
    return 1 / (1 + math.exp(-x))


In [3]:
BATCH_SIZE=32

In [4]:
import lightning.__version__ as v
v

'2.1.3'

In [5]:
tensorboard = pl.loggers.TensorBoardLogger(save_dir="")
torch.cuda.is_available()


/home/seb/Perso/git/sudoku/sudoku_clean_v2/venv/lib/python3.10/site-packages/torch/cuda/__init__.py:83: UserWarning: CUDA initialization: CUDA unknown error - this may be due to an incorrectly set up environment, e.g. changing env variable CUDA_VISIBLE_DEVICES after program start. Setting the available devices to be zero. (Triggered internally at  ../c10/cuda/CUDAFunctions.cpp:109.)
  return torch._C._cuda_getDeviceCount() > 0


False

In [6]:
seed_everything(seed=1)

Global seed set to 1


1

In [7]:
# train_dataset, val_dataset = get_datasets(train_size=1280, test_size=1280)
# train_dataloader = DataLoader(train_dataset, batch_size=32)
# val_dataloader = DataLoader(val_dataset, batch_size=32)

In [8]:
# model = SudokuLightning.load_from_checkpoint(checkpoint_path="/home/seb/Perso/git/sudoku/sudoku_clean_v2/checkpoints/epoch=9-step=4961.ckpt")
model = SudokuTrialErrorLightning.load_from_checkpoint(checkpoint_path="model_9_m3_5epoch.ckpt")
# model = SudokuLightning.load_from_checkpoint(checkpoint_path="/home/seb/Perso/git/sudoku/sudoku_clean_v2/lightning_logs/version_21/checkpoints/epoch=99-step=105059.ckpt")#"model_8_m3_100epoch.ckpt")
# /home/seb/Perso/git/sudoku/sudoku_clean_v2/lightning_logs/version_21/checkpoints/epoch=99-step=105059.ckpt

/home/seb/Perso/git/sudoku/sudoku_clean_v2/venv/lib/python3.10/site-packages/torch/nn/_reduction.py:42: UserWarning: size_average and reduce args will be deprecated, please use reduction='none' instead.
  warnings.warn(warning.format(ret))


In [9]:
# test_x, test_y = tuple(next(iter(test_dataset)))
# test_x = test_x.reshape(1,2,729)
# test_y = test_y.reshape(1,2,729)

In [10]:
def str_to_row_col_grid(su_str):
    su_str = su_str.replace('.','0')
    assert len(su_str)==81
    return [[int(su_str[j*9+i]) for i in range(9)] for j in range(9)]

In [11]:
grid_17 = [
    [1,0,0, 0,0,0, 5,2,0],
    [0,0,0, 0,7,8, 0,0,0],
    [0,0,0, 0,0,0, 6,0,0],

    [0,9,0, 0,4,0, 0,0,0],
    [0,0,0, 5,0,0, 1,0,0],
    [0,7,0, 0,0,0, 0,0,0],

    [0,0,6, 2,0,0, 0,0,0],
    [0,4,0, 0,0,0, 0,7,8],
    [0,0,0, 0,0,0, 0,0,3],

]

In [25]:
grid_evil_0 = [
    [0,0,0, 1,6,0, 2,0,0],
    [0,3,0, 0,0,5, 0,0,4],
    [0,0,7, 0,0,0, 0,9,0],

    [0,0,1, 0,0,0, 0,8,2],
    [3,0,0, 7,0,4, 0,0,5],
    [4,2,0, 0,0,0, 6,0,0],

    [0,8,0, 0,0,0, 5,0,0],
    [7,0,0, 8,0,0, 0,2,0],
    [0,0,6, 0,5,1, 0,0,0],

]
grid_evil_1 = [
    [0,0,0, 2,0,0, 0,0,0],
    [0,0,9, 7,0,0, 3,8,0],
    [3,6,0, 0,0,0, 0,7,0],

    [1,0,6, 8,0,0, 0,0,0],
    [0,0,0, 3,5,9, 0,0,0],
    [0,0,0, 0,0,2, 8,0,5],

    [0,4,0, 0,0,0, 0,9,1],
    [0,2,5, 0,0,8, 7,0,0],
    [0,0,0, 0,0,6, 0,0,0],
]
grid_evil_2 = [
    [0,2,0, 1,0,0, 0,7,0],
    [0,0,0, 3,0,2, 0,0,0],
    [0,0,1, 0,8,0, 0,4,0],

    [9,0,0, 0,1,0, 0,0,7],
    [0,0,8, 0,6,0, 0,5,0],
    [0,0,0, 0,0,0, 0,0,0],

    [0,8,0, 0,3,6, 0,0,9],
    [0,0,5, 0,7,0, 0,0,6],
    [0,0,2, 0,0,0, 0,0,3],
]

In [13]:
# get_grid_number_soluce(grid_17)
# it took 8min39s to return 1

In [15]:
def build_tensor_out_of_grid(grid):
    np_grid = np.asarray(grid) 
    big_grid = np.zeros((1,2,9,9,9), dtype=np.float32)
    for i in range(9):
        big_grid[0,1,:,:,i] = (np_grid==i+1)
        big_grid[0,0,:,:,i] = ((np_grid!=i+1) & (np_grid!=0))
    return torch.from_numpy(big_grid).view(1,2,729)
    

In [23]:
def solve_from_grid(grid, display_grids=True):
    test_x = build_tensor_out_of_grid(grid)
    i = 0

    print(i, test_x.sum())
    if display_grids:
        display(display_as_dataframe(test_x))
    new_X = model.predict(test_x)
    print(i, new_X.sum())
    if display_grids:
        display(display(display_as_dataframe(new_X)))
    while new_X.sum()<729:
        new_X = model.predict(new_X)
        print(i, new_X.sum())
        i+=1
        if display_grids:
            display(display_as_dataframe(new_X))
    return new_X

In [24]:
solve_from_grid(grid_evil_0, display_grids=False)

0 tensor(234.)
0 tensor(538.)
0 tensor(551.)
1 tensor(573.)
2 tensor(576.)
3 tensor(584.)
4 tensor(587.)
5 tensor(589.)
6 tensor(590.)
7 tensor(591.)
8 tensor(595.)
9 tensor(596.)
10 tensor(598.)
11 tensor(607.)
12 tensor(609.)
13 tensor(616.)
14 tensor(619.)
15 tensor(632.)
16 tensor(635.)
17 tensor(644.)
18 tensor(653.)
19 tensor(666.)
20 tensor(669.)
21 tensor(674.)
22 tensor(678.)
23 tensor(686.)
24 tensor(692.)
25 tensor(703.)
26 tensor(713.)
27 tensor(724.)
28 tensor(729.)


tensor([[[1., 1., 1.,  ..., 1., 1., 0.],
         [0., 0., 0.,  ..., 0., 0., 1.]]])

In [28]:
solve_from_grid(grid_evil_1, display_grids=False)

0 tensor(225.)
0 tensor(533.)
0 tensor(544.)
1 tensor(561.)
2 tensor(570.)
3 tensor(575.)
4 tensor(579.)
5 tensor(582.)
6 tensor(584.)
7 tensor(585.)
8 tensor(586.)
9 tensor(592.)
10 tensor(596.)
11 tensor(605.)
12 tensor(608.)
13 tensor(613.)
14 tensor(614.)
15 tensor(618.)
16 tensor(623.)
17 tensor(637.)
18 tensor(638.)
19 tensor(641.)
20 tensor(644.)
21 tensor(649.)
22 tensor(651.)
23 tensor(656.)
24 tensor(664.)
25 tensor(678.)
26 tensor(682.)
27 tensor(688.)
28 tensor(695.)
29 tensor(704.)
30 tensor(714.)
31 tensor(722.)
32 tensor(727.)
33 tensor(729.)


tensor([[[1., 1., 1.,  ..., 1., 0., 1.],
         [0., 0., 0.,  ..., 0., 1., 0.]]])

In [26]:
solve_from_grid(grid_evil_2, display_grids=False)

0 tensor(207.)
0 tensor(491.)
0 tensor(510.)
1 tensor(522.)
2 tensor(526.)
3 tensor(534.)
4 tensor(536.)
5 tensor(544.)
6 tensor(547.)
7 tensor(565.)
8 tensor(568.)
9 tensor(581.)
10 tensor(588.)
11 tensor(610.)
12 tensor(619.)
13 tensor(634.)
14 tensor(650.)
15 tensor(665.)
16 tensor(674.)
17 tensor(680.)
18 tensor(687.)
19 tensor(694.)
20 tensor(702.)
21 tensor(710.)
22 tensor(720.)
23 tensor(727.)
24 tensor(729.)


tensor([[[1., 1., 1.,  ..., 1., 1., 1.],
         [0., 0., 0.,  ..., 0., 0., 0.]]])

In [19]:
solve_from_grid(grid_17)

0 tensor(153.)


0 tensor(431.)


None

0 tensor(449.)


1 tensor(469.)


...

71 tensor(709.)


72 tensor(717.)


73 tensor(726.)


74 tensor(729.)


tensor([[[0., 1., 1.,  ..., 1., 1., 1.],
         [1., 0., 0.,  ..., 0., 0., 0.]]])